In [1]:
import sys, time, pickle, torch
sys.path.insert(0, '../Models')
sys.path.insert(0, '../Utils')
sys.path.insert(0, '../Preprocess')
import numpy as np
import pandas as pd
from ann import NeuralNet
from utils import my_completely_random_sample, conv_input_attri_to_word_attri,\
    collect_info_for_metric, save_info, random_state, load_prev_samples, prep_text_for_view
from preprocess_funcs import preprocess_pipelined, prepare_text, prepare_text_view_friendly

[nltk_data] Downloading package stopwords to /home/user/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /home/user/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
model = torch.load('../Models/ann_model.pt')

In [3]:
Train_df = pd.read_csv('../Data/Processed/train_df.csv')
Test_df = pd.read_csv('../Data/Processed/test_df.csv')
Y_train = Train_df['sentiment']
Y_test = Test_df['sentiment']
Y_train_tensor = torch.tensor(Y_train, dtype=torch.float).unsqueeze(dim=1)
Y_test_tensor = torch.tensor(Y_test, dtype=torch.float).unsqueeze(dim=1)


In [4]:
reviews_raw, targets, indices = my_completely_random_sample(Train_df, num_sample=50)

In [5]:
# reviews_raw, targets, indices = load_prev_samples(Train_df, 'lime_outs.pkl')

In [6]:
reviews_raw[4]

'Directed and co-written by Eytan Fox the writer/director of the highly acclaimed 2002 mini feature "Yossi & Jagger" (2002). This comparative epic, at 1hr 53 minutes, is another fine romantic drama in which we must deal with tragedy as well as celebrate the beauty and joy in life. Westerners, especially urban gay men like myself, need to be moved outside our safety zone and be informed of the real life and death struggle elsewhere to be able to love with equity.<br /><br />While "Yossi & Jagger" focused on a pair of gay lovers in the closeted confines of Israeli military service, "Ha Buah" is centred on a group of civilian friends, both straight and gay, who share a unit in the heart of Israel\'s generally gay-tolerant, but not always gay-friendly, capital Tel Aviv.<br /><br />"Ha Buah" opens with a dramatic border check point scene in which Noam (Ohad Knoller \x96 Yossi from "Yossi & Jagger") first meets handsome young Arab Ashraf (Yousef Sweid). Romance soon blooms \x96 but in that p

In [7]:
prep_text_for_view(reviews_raw[4])

['Directed',
 'and',
 'co-written',
 'by',
 'Eytan',
 'Fox',
 'the',
 'writer/director',
 'of',
 'the',
 'highly',
 'acclaimed',
 '2002',
 'mini',
 'feature',
 '"Yossi',
 '&',
 'Jagger"',
 '(2002).',
 'This',
 'comparative',
 'epic,',
 'at',
 '1hr',
 '53',
 'minutes,',
 'is',
 'another',
 'fine',
 'romantic',
 'drama',
 'in',
 'which',
 'we',
 'must',
 'deal',
 'with',
 'tragedy',
 'as',
 'well',
 'as',
 'celebrate',
 'the',
 'beauty',
 'and',
 'joy',
 'in',
 'life.',
 'Westerners,',
 'especially',
 'urban',
 'gay',
 'men',
 'like',
 'myself,',
 'need',
 'to',
 'be',
 'moved',
 'outside',
 'our',
 'safety',
 'zone',
 'and',
 'be',
 'informed',
 'of',
 'the',
 'real',
 'life',
 'and',
 'death',
 'struggle',
 'elsewhere',
 'to',
 'be',
 'able',
 'to',
 'love',
 'with',
 'equity.br',
 '',
 'While',
 '"Yossi',
 '&',
 'Jagger"',
 'focused',
 'on',
 'a',
 'pair',
 'of',
 'gay',
 'lovers',
 'in',
 'the',
 'closeted',
 'confines',
 'of',
 'Israeli',
 'military',
 'service,',
 '"Ha',
 'Buah"',


In [8]:
#define some containers to save some info
model_out_list, attr_list = [], []

In [9]:
from captum.attr import DeepLift
from captum.attr import visualization 

In [10]:
# lime = Lime(forward_func=model.forward)
deep_lift = DeepLift(model)

In [11]:
def generate_record(raw_review, target):
    data, data_vec, input_tfidf = preprocess_pipelined([raw_review]) #preprocess_pipelined expects a lits of strings        
    input_model = input_tfidf.to_dense()
    with torch.no_grad():
        pred_prob =  model.forward(input_model).detach().item()
        pred_class = 'Pos' if pred_prob > 0.5 else 'Neg' 
        true_class = 'Pos' if target > 0.5 else 'Neg' 
        attribution, delta = deep_lift.attribute(input_model, return_convergence_delta=True)
        attr_score = torch.sum(attribution)    
        attr_class = 'Pos' if attr_score > 0.5 else 'Neg'
        raw_input = prep_text_for_view(raw_review) #raw_review.split()
        convergence_score = delta
        print(f'orig attri nonzero: {attribution.nonzero()}')
        word_attributions = conv_input_attri_to_word_attri(attribution, raw_review)
        #         print(f'word attributions {word_attributions}')
        #         print(f'pred_prob {pred_prob}')
        #         print(f'pred_class {pred_class}')
        #         print(f'true_class {true_class}')
        #         print(f'attribution {attribution}')
        #         print(f'attr_class {attr_class}')
        #         print(f'attr_score {attr_score}')
#         print(f'raw_input {raw_input}')

        
        #collect info for metrics later
        collect_info_for_metric(model_out_list, pred_prob, attr_list, attribution)
        
    
        visual_record = visualization.VisualizationDataRecord(word_attributions=word_attributions,
                                                         pred_prob=pred_prob,
                                                         pred_class=pred_class,
                                                         true_class=true_class,
                                                         attr_class=attr_class,
                                                         attr_score=attr_score,
                                                         raw_input=raw_input,
                                                         convergence_score=convergence_score)
        
        
        return visual_record
      
    

In [12]:
for i, (rev_raw, target) in enumerate(zip(reviews_raw, targets), start=1):
    visual_record = generate_record(rev_raw, target)
    print(visualization.visualize_text([visual_record])) #list because visualize_text expects a list of visual_records

/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/torch/nn/functional.py:1806: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/captum/_utils/gradient.py:57: UserWarning: Input Tensor 0 did not already require gradients, required_grads has been set automatically.
  warnings.warn(
/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/captum/attr/_core/deep_lift.py:322: UserWarning: Setting forward, backward hooks and attributes on non-linear
               activations. The hooks and attributes will be removed
            after the attribution is finished
  warnings.warn(


orig attri nonzero: tensor([[    0,   349],
        [    0,   358],
        [    0,   365],
        [    0,   888],
        [    0,  1667],
        [    0,  1716],
        [    0,  1924],
        [    0,  1937],
        [    0,  2262],
        [    0,  4241],
        [    0,  4342],
        [    0,  4854],
        [    0,  6083],
        [    0,  6405],
        [    0,  7016],
        [    0,  7047],
        [    0,  7210],
        [    0,  7570],
        [    0,  8576],
        [    0,  8661],
        [    0,  8671],
        [    0,  8767],
        [    0,  9078],
        [    0,  9155],
        [    0, 10154],
        [    0, 10214],
        [    0, 10713],
        [    0, 10846],
        [    0, 10940],
        [    0, 11320],
        [    0, 11492],
        [    0, 11500],
        [    0, 11557],
        [    0, 12789],
        [    0, 13426],
        [    0, 13449],
        [    0, 13640],
        [    0, 13704],
        [    0, 13716],
        [    0, 14456],
        [    0, 1458

<IPython.core.display.HTML object>
orig attri nonzero: tensor([[    0,  1620],
        [    0,  1667],
        [    0,  2149],
        [    0,  3001],
        [    0,  3004],
        [    0,  4509],
        [    0,  4523],
        [    0,  5233],
        [    0,  5424],
        [    0,  5468],
        [    0,  5809],
        [    0,  6017],
        [    0,  6997],
        [    0,  8395],
        [    0,  8574],
        [    0,  8671],
        [    0, 10223],
        [    0, 13241],
        [    0, 13299],
        [    0, 13314],
        [    0, 13526],
        [    0, 13561],
        [    0, 13637],
        [    0, 13716],
        [    0, 14249],
        [    0, 14299],
        [    0, 16852],
        [    0, 17115],
        [    0, 17482],
        [    0, 17741],
        [    0, 18252],
        [    0, 18531],
        [    0, 18940],
        [    0, 19898],
        [    0, 20218],
        [    0, 20361],
        [    0, 20845],
        [    0, 21797],
        [    0, 23038],
        [

<IPython.core.display.HTML object>
orig attri nonzero: tensor([[    0,    39],
        [    0,   860],
        [    0,  1620],
        [    0,  1652],
        [    0,  6675],
        [    0,  7047],
        [    0,  8671],
        [    0, 11557],
        [    0, 16401],
        [    0, 16634],
        [    0, 17247],
        [    0, 17979],
        [    0, 18502],
        [    0, 18573],
        [    0, 19898],
        [    0, 20521],
        [    0, 23038],
        [    0, 23039],
        [    0, 27955],
        [    0, 29662],
        [    0, 30779],
        [    0, 33869],
        [    0, 38399],
        [    0, 42795],
        [    0, 43977],
        [    0, 43982],
        [    0, 43999],
        [    0, 49034],
        [    0, 53384],
        [    0, 53565],
        [    0, 54737],
        [    0, 55321],
        [    0, 55324],
        [    0, 58098],
        [    0, 58806],
        [    0, 67275],
        [    0, 70297],
        [    0, 73383]])
words attr: {'10': tensor(1.), '

<IPython.core.display.HTML object>
orig attri nonzero: tensor([[    0,  1712],
        [    0,  2980],
        [    0,  3689],
        [    0,  5006],
        [    0,  5468],
        [    0,  6997],
        [    0,  7210],
        [    0,  7434],
        [    0,  8671],
        [    0,  9982],
        [    0, 10914],
        [    0, 11640],
        [    0, 13271],
        [    0, 13439],
        [    0, 14243],
        [    0, 16775],
        [    0, 18296],
        [    0, 20510],
        [    0, 22205],
        [    0, 22822],
        [    0, 26583],
        [    0, 27936],
        [    0, 28431],
        [    0, 28751],
        [    0, 30693],
        [    0, 30991],
        [    0, 31167],
        [    0, 31223],
        [    0, 38605],
        [    0, 39420],
        [    0, 40269],
        [    0, 41241],
        [    0, 43982],
        [    0, 43999],
        [    0, 45041],
        [    0, 46640],
        [    0, 47003],
        [    0, 47078],
        [    0, 50021],
        [

...

<IPython.core.display.HTML object>
orig attri nonzero: tensor([[    0,  1652],
        [    0,  1654],
        [    0,  1667],
        [    0,  3824],
        [    0,  4509],
        [    0,  6110],
        [    0,  7434],
        [    0,  8671],
        [    0, 12135],
        [    0, 13565],
        [    0, 18138],
        [    0, 18502],
        [    0, 18511],
        [    0, 20078],
        [    0, 21549],
        [    0, 21688],
        [    0, 21842],
        [    0, 23270],
        [    0, 24036],
        [    0, 24441],
        [    0, 25883],
        [    0, 27833],
        [    0, 27955],
        [    0, 28431],
        [    0, 33181],
        [    0, 33730],
        [    0, 34379],
        [    0, 38605],
        [    0, 38721],
        [    0, 38894],
        [    0, 38922],
        [    0, 39214],
        [    0, 40279],
        [    0, 41658],
        [    0, 43693],
        [    0, 43982],
        [    0, 45364],
        [    0, 45724],
        [    0, 50102],
        [

<IPython.core.display.HTML object>
orig attri nonzero: tensor([[    0,  1614],
        [    0,  2045],
        [    0,  3004],
        [    0,  3370],
        [    0,  3813],
        [    0,  4501],
        [    0,  5078],
        [    0,  5233],
        [    0,  5468],
        [    0,  7160],
        [    0,  7210],
        [    0,  7492],
        [    0,  8671],
        [    0, 11661],
        [    0, 12704],
        [    0, 12759],
        [    0, 12986],
        [    0, 13439],
        [    0, 15839],
        [    0, 17261],
        [    0, 17287],
        [    0, 17742],
        [    0, 19961],
        [    0, 20308],
        [    0, 23066],
        [    0, 24383],
        [    0, 27202],
        [    0, 27955],
        [    0, 29119],
        [    0, 29952],
        [    0, 30987],
        [    0, 32259],
        [    0, 33325],
        [    0, 38588],
        [    0, 39222],
        [    0, 40529],
        [    0, 43982],
        [    0, 44934],
        [    0, 44936],
        [

<IPython.core.display.HTML object>
orig attri nonzero: tensor([[    0,    39],
        [    0,  1620],
        [    0,  4501],
        [    0,  5216],
        [    0,  5468],
        [    0,  8533],
        [    0,  8671],
        [    0, 11809],
        [    0, 16064],
        [    0, 16865],
        [    0, 21713],
        [    0, 21842],
        [    0, 21973],
        [    0, 22399],
        [    0, 23041],
        [    0, 23388],
        [    0, 24108],
        [    0, 24441],
        [    0, 24486],
        [    0, 28431],
        [    0, 36463],
        [    0, 38063],
        [    0, 38605],
        [    0, 39409],
        [    0, 40222],
        [    0, 40439],
        [    0, 41658],
        [    0, 43581],
        [    0, 43982],
        [    0, 47419],
        [    0, 50010],
        [    0, 51125],
        [    0, 53627],
        [    0, 53867],
        [    0, 54067],
        [    0, 57502],
        [    0, 62657],
        [    0, 63568],
        [    0, 64400],
        [

<IPython.core.display.HTML object>
orig attri nonzero: tensor([[    0,    39],
        [    0,  1231],
        [    0,  1667],
        [    0,  2715],
        [    0,  4408],
        [    0,  4501],
        [    0,  5468],
        [    0,  6677],
        [    0,  7801],
        [    0,  7836],
        [    0,  8472],
        [    0,  9982],
        [    0, 10223],
        [    0, 10367],
        [    0, 11661],
        [    0, 11775],
        [    0, 12511],
        [    0, 12618],
        [    0, 15078],
        [    0, 15899],
        [    0, 17358],
        [    0, 18135],
        [    0, 18282],
        [    0, 19841],
        [    0, 19961],
        [    0, 20211],
        [    0, 21973],
        [    0, 22901],
        [    0, 23270],
        [    0, 24441],
        [    0, 25363],
        [    0, 25365],
        [    0, 25999],
        [    0, 26123],
        [    0, 26143],
        [    0, 26225],
        [    0, 27851],
        [    0, 29157],
        [    0, 29161],
        [

<IPython.core.display.HTML object>


In [15]:
save_info(indices, reviews_raw, targets, model_out_list, attr_list, fname='deep_lift_out.pkl')

{'indices': [3555,
  23474,
  13833,
  12237,
  4632,
  9114,
  327,
  844,
  24631,
  17758,
  5654,
  19637,
  1462,
  24567,
  8536,
  1013,
  13913,
  8203,
  12999,
  20936,
  10982,
  866,
  22731,
  19996,
  6293,
  18922,
  13688,
  12690,
  24838,
  3707,
  5811,
  5400,
  3285,
  2277,
  4026,
  15629,
  12084,
  14787,
  2421,
  13503,
  21742,
  338,
  18429,
  14404,
  7464,
  8679,
  16240,
  20882,
  15145,
  6782,
  13615,
  24420,
  8581,
  21797,
  10057,
  15051,
  21480,
  153,
  18810,
  16401,
  8940,
  12167,
  21933,
  22489,
  14061,
  1267,
  24227,
  5876,
  19832,
  11042,
  7307,
  23696,
  3962,
  16021,
  10652,
  75,
  11424,
  74,
  22711,
  10178,
  18522,
  1427,
  11155,
  5434,
  7696,
  21546,
  24579,
  17529,
  21464,
  15887,
  12967,
  7162,
  19841,
  2706,
  21057,
  4097,
  4939,
  15201,
  2310,
  18632],
 'raw_reviews': ['This musical was not quite what I expected, foremost being there weren\'t many scenes between Brando and Sinatra. As it

In [14]:
# from lime.lime_text import LimeTextExplainer
# explainer = LimeTextExplainer(
#     class_names = ['negative', 'positive'],
#     bow=True
#   )

# def lime_pred_sentence(sentence):
#     if isinstance(sentence, str):
#         sentence = [sentence]
#     sent_prepped, sent_vec, sent_tensor = preprocess_pipelined(sentence)
#     print(f'sent tensor size {sent_tensor.size()}')
#     with torch.no_grad():
#         out = model(sent_tensor)
#         out_complement = 1-out
#         out_concat = torch.cat([out_complement, out], dim=1)
#         out_concat_np = out_concat.detach().numpy()
    
# #         print(f'{sent_prepped}')
# #         print(f'{sent_vec}')
# #         print(f'{sent_tensor}')
# #         print(f'{out_concat_np.shape}')
#         return out_concat_np

# for r in reviews_raw:
#     explanation = explainer.explain_instance(r, lime_pred_sentence)
#     explanation.show_in_notebook()